In [1]:
import pandas as pd
import numpy as np
import pandas as pd
import nltk
from nltk.corpus import wordnet
import string
from nltk import pos_tag
from nltk.corpus import stopwords
from nltk.tokenize import WhitespaceTokenizer
from nltk.stem import WordNetLemmatizer
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.decomposition import LatentDirichletAllocation
from sklearn.feature_extraction.text import CountVectorizer
import pyLDAvis
import re
import multiprocessing as mp
from nltk.tokenize import word_tokenize, sent_tokenize
import string
from nltk.corpus import stopwords
import time
import timeit
import spacy
from dframcy import DframCy
import timeit
import warnings
from nltk.tokenize import sent_tokenize
from ast import literal_eval
import gensim
from gensim.models import TfidfModel
import gensim.corpora as corpora
import os
import pyLDAvis.gensim_models
from tqdm import tqdm

import clean_parallel
cp = clean_parallel.cp()

import clean_parallel_init
cpt = clean_parallel_init.cpt()

D:\Program Files (x86)\Python\lib\site-packages\scipy\sparse\sparsetools.py:21: DeprecationWarning: `scipy.sparse.sparsetools` is deprecated!
scipy.sparse.sparsetools is a private module for scipy.sparse, and should not be used.
  _deprecated()


In [2]:
def get_wordnet_pos(pos_tag):
        if pos_tag.startswith('J'):
            return wordnet.ADJ
        elif pos_tag.startswith('V'):
            return wordnet.VERB
        elif pos_tag.startswith('N'):
            return wordnet.NOUN
        elif pos_tag.startswith('R'):
            return wordnet.ADV
        else:
            return wordnet.NOUN
    
def text_clean (text):
    # lower text
    text = text.lower()
    # tokenize text
    text = " ".join([word for word in text.rsplit()])
    # remove punctuation and multiple spaces
    text = "".join([word.strip(string.punctuation) or  " " for word in text]).split()
    # remove weird quotation marks
    text = [word.replace('”',"").replace('“',"").replace('’','') for word in text]
    # remove words that contain numbers
    text = [word for word in text if not any(c.isdigit() for c in word)]
    # remove stop words
    stop = stopwords.words('english')
    text = [x for x in text if x not in stop]
    # remove empty tokens
    text = [t for t in text if len(t) > 0]
    # pos tag text
    pos_tags = pos_tag(text)
    # lemmatize text
    text = [WordNetLemmatizer().lemmatize(t[0], get_wordnet_pos(t[1])) for t in pos_tags]
    # remove words with only one letter
    text = [t for t in text if len(t) > 1]
    # join all
    text = " ".join(text)

    return(text)

def clean (data): #change so output is a list or array (also mybe a for loop and parallel)
        data['clean'] = data[0].apply(lambda x: text_clean(x))
        return (data['clean'])
    
def vectorization (data):
        vectorizer = TfidfVectorizer()
        cleaned = vectorizer.fit_transform(data)
        return (cleaned)
    
def get_topics(components, feature_names, n=50):
        for idx, topic in enumerate(components):
            print("\nTopic %d: " % (idx+1), 
                  [(feature_names[i], topic[i].round(2)) 
                   for i in topic.argsort()[:-n - 1:-1]])
    
def display_topics(model, feature_names, no_top_words):
        topic_dict = {}
        for topic_idx, topic in enumerate(model.components_):
            topic_dict["Topic %d words" % (topic_idx)]= ['{}'.format(feature_names[i])
                        for i in topic.argsort()[:-no_top_words - 1:-1]]
            topic_dict["Topic %d weights" % (topic_idx)]= ['{:.1f}'.format(topic[i])
                        for i in topic.argsort()[:-no_top_words - 1:-1]]
        return pd.DataFrame(topic_dict)
    
def topic_analysis (data, number_of_topics = 10):
        
        vectorizer = CountVectorizer()
        clean = vectorizer.fit_transform(data)
        feature_names = vectorizer.get_feature_names_out()
        lda = LatentDirichletAllocation(n_components=number_of_topics,
                                        random_state=27, 
                                        n_jobs=-1)
        lda.fit(clean)
        
        topic_df = display_topics (lda, feature_names, 30)
        return (topic_df, lda, clean, feature_names)
    
def topic_visualization (data, number_of_topics=10):
        
        topic_df, lda, clean, feature_names = topic_analysis(data = data, number_of_topics = number_of_topics)
        
        topic_term_dists = lda.components_ / lda.components_.sum(axis=1)[:, None]
        doc_lengths = clean.sum(axis=1).getA1()
        term_frequency = clean.sum(axis=0).getA1()
        lda_doc_topic_dists = lda.transform(clean)
        doc_topic_dists = lda_doc_topic_dists / lda_doc_topic_dists.sum(axis=1)[:, None]
        vocab = feature_names
        
        lda_pyldavis = pyLDAvis.prepare(topic_term_dists, doc_topic_dists, doc_lengths, vocab, term_frequency)
        return(lda_pyldavis)


In [3]:
def split_sentence(data):
    data_list = list(data)
    tokens = []
    for doc in nlp.pipe(data_list, disable = ["tagger", 
                                                 "parser", 
                                                 "attribute_ruler", 
                                                 "lemmatizer","ner","textcat"]):
        a = []
        for token in doc:
            if token.is_sent_start==True:
                tokens.append(a)
                a = []
                a.append(token.text)
            else:
                a.append(token.text)
        b = []
        for sentence in tokens:
            b.append(" ".join([words for words in sentence]))
    return(b)

def clean_mlm(text):
    
    # split into sentences:
    text = text.lower()
    text_sentence = sent_tokenize(text)
    token_list = []
    table = str.maketrans('', '', string.punctuation)
    stop_words = stopwords.words('english')
    
    for sentence in text_sentence:
        tokens = word_tokenize(sentence)
        tokens = [w.translate(table) for w in tokens]
        tokens = [word for word in tokens if word.isalpha()]
        tokens = [w for w in tokens if not w in stop_words]
        tokens = [w for w in tokens if len(w)>0]
        pos_tags = pos_tag(tokens)
        tokens = [WordNetLemmatizer().lemmatize(t[0], get_wordnet_pos(t[1])) for t in pos_tags]
        tokens = [t for t in tokens if len(t) > 1]
        
        token_list.append(tokens)
    
    return token_list

def clean_mlm_parallel(text):
    return (clean_mlm(text))

# PARALLEL MLML ON ENTIER DATA
def b(data):
    pool = mp.Pool(mp.cpu_count())

    results = []
    for result in tqdm(pool.imap(cp.clean_mlm_parallel, [article for article in data]), total=len(data)):
        results.append(result)
    #results = pool.map(cp.clean_mlm_parallel, [article for article in data])

    pool.close()
    return results
    
# PARALEL CLASSIC ON ENTIRE DATA
def a(data):
    list_sentence_nltk = split_sentence_nltk (data[0])
    df_sentence_nltk = pd.DataFrame({0:list_sentence_nltk})
    df_sentence_nltk = pd.DataFrame({0:df_sentence_nltk[0].explode()})
    df_sentence_nltk = df_sentence_nltk.reset_index(drop=True)
    df_sentence_nltk = df_sentence_nltk.replace(r'^s*$', float('NaN'), regex = True).dropna()

    pool = mp.Pool(mp.cpu_count())

    results = pool.map(cp.clean_parallel, [article for article in df_sentence_nltk[0]])

    pool.close()
    return results
    
def idk(data):
    list_sentence_nltk = sent_tokenize(data)
    df_sentence_nltk = pd.DataFrame({0:list_sentence_nltk})
    df_sentence_nltk = pd.DataFrame({0:df_sentence_nltk[0].explode()})
    df_sentence_nltk = df_sentence_nltk.reset_index(drop=True)
    df_sentence_nltk = df_sentence_nltk.replace(r'^s*$', float('NaN'), regex = True).dropna()
    clean_sentence_nltk = clean(df_sentence_nltk)
    return(clean_sentence_nltk)

def split_sentence_nltk (data):
    data_list = list(data)
    return ([sent_tokenize(text) for text in data_list])

In [ ]:
data_test = data[0]

g_var = None
def init_worker(X):
    global g_var
    g_var = X

def clean_init(i):
    text = g_var[i]
    

pool = mp.Pool(processes = mp.cpu_count(), initializer=init_worker, initargs=(data_test))

#results = []
#for result in tqdm(pool.imap(cp.clean_mlm_parallel, [article for article in data]), total=len(data)):
#    results.append(result)
results = pool.map(cp.clean_mlm_parallel, range())

    pool.close()

In [9]:
spacy.prefer_gpu()
nlp = spacy.load("en_core_web_trf")
nlp.add_pipe('sentencizer')
dframcy = DframCy(nlp)
doc = dframcy.nlp("This is a text, This too is a text? i am writing this to you, i am going to kill frank.")
df_a = dframcy.to_dataframe(doc)

D:\Program Files (x86)\Python\lib\site-packages\thinc\util.py:312: DeprecationWarning: This function is deprecated in favor of cupy.from_dlpack
  return cupy.fromDlpack(torch.utils.dlpack.to_dlpack(torch_tensor))
D:\Program Files (x86)\Python\lib\site-packages\thinc\util.py:312: DeprecationWarning: This function is deprecated in favor of cupy.from_dlpack
  return cupy.fromDlpack(torch.utils.dlpack.to_dlpack(torch_tensor))


In [189]:
list_sentence_nltk = split_sentence_nltk(df['content'])
df_sentence_nltk = pd.DataFrame({0:list_sentence_nltk})
df_sentence_nltk = pd.DataFrame({0:df_sentence_nltk[0].explode()})
df_sentence_nltk = df_sentence_nltk.reset_index(drop=True)
df_sentence_nltk = df_sentence_nltk.replace(r'^s*$', float('NaN'), regex = True).dropna()
clean_sentence_nltk = clean(df_sentence_nltk)

In [201]:
data_words_nltk = list(sent_to_words(clean_sentence_nltk))
data_nltk_final = data_bigrams_trigrams(data_words_nltk)
id2word_nltk, texts_nltk, corpus_nltk = prep_for_lda_gensim(data_nltk_final, 0.03)

In [98]:
lda_model_nltk = gensim.models.ldamulticore.LdaMulticore(corpus=corpus_nltk[:-1],
                                           id2word=id2word_nltk,
                                           num_topics=50,
                                           random_state=100,
                                           #update_every=1,
                                           chunksize=100,
                                           passes=10, workers = os.cpu_count())
                                           #alpha="auto")

In [99]:
vis_nltk = pyLDAvis.gensim_models.prepare(lda_model_nltk,corpus_nltk, id2word_nltk, mds='mmds')
pyLDAvis.display(vis_nltk)

D:\Program Files (x86)\Python\lib\site-packages\pyLDAvis\_prepare.py:247: FutureWarning: In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only
  by='saliency', ascending=False).head(R).drop('saliency', 1)


In [108]:
df_full = pd.DataFrame({0:df['content']})
clean_full = clean(df_full)
data_words_full = list(sent_to_words(clean_full))
data_full_final = data_bigrams_trigrams(data_words_full)
id2word_full, texts_full, corpus_full = prep_for_lda_gensim(data_full_final, 0.01)

In [109]:
lda_model_full = gensim.models.ldamulticore.LdaMulticore(corpus=corpus_full[:-1],
                                           id2word=id2word_full,
                                           num_topics=50,
                                           random_state=100,
                                           #update_every=1,
                                           chunksize=100,
                                           passes=10)
                                           #alpha="auto")

In [110]:
vis_full = pyLDAvis.gensim_models.prepare(lda_model_full,corpus_full, id2word_full, mds='mmds')
pyLDAvis.display(vis_full)

D:\Program Files (x86)\Python\lib\site-packages\pyLDAvis\_prepare.py:247: FutureWarning: In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only
  by='saliency', ascending=False).head(R).drop('saliency', 1)


In [4]:
def sent_to_words(sentences):
    for sentence in sentences:
        yield(gensim.utils.simple_preprocess(str(sentence), deacc=True))  # deacc=True removes punctuations

#data_words = list(sent_to_words(clean_sentence))

In [5]:
#bi tri grams
def bigram_phrase (data_words):
    bigram_phrases = gensim.models.Phrases(data_words, min_count=5, threshold = 50)
    bigram = gensim.models.phrases.Phraser(bigram_phrases)
    return bigram, bigram_phrases

def trigram_phrase (data_words, bigram_phrases):
    trigram_phrases = gensim.models.Phrases(bigram_phrases[data_words], threshold=50)
    trigram = gensim.models.phrases.Phraser(trigram_phrases)
    return trigram
    
def make_bigrams(text, bigram):
    return [bigram[doc] for doc in text]

def make_trigrams(text, trigram):
    return [trigram[doc] for doc in text]

def data_bigrams_trigrams (data_words):
    bigram, bigram_phrases = bigram_phrase(data_words)
    trigram = trigram_phrase (data_words, bigram_phrases)
    data_bigrams = make_bigrams(data_words, bigram)
    data_bigrams_trigrams = make_trigrams(data_bigrams, trigram)
    return data_bigrams_trigrams

In [241]:
df_sentence_final_2 = []
for sentence in data_bigrams_trigrams:
    df_sentence_final_2.append(" ".join(sentence))
df_sentence_final_2[1:5]

['get morning_brief_send directly_inbox_every monday friday et',
 'subscribe_monday february corporate_america launch two bird putin backyard invasion_ukraine',
 'airplane one finger hand',
 'first round action host multinational company begin trickle weekend transport giant fedex ups suspend shipment russia']

In [6]:
#TF-IDF REMOVAL
def prep_for_lda_gensim (data, low_value):
    id2word = corpora.Dictionary(data)

    texts = data

    corpus = [id2word.doc2bow(text) for text in texts]
# print (corpus[0][0:20])

    tfidf = TfidfModel(corpus, id2word=id2word)

    #low_value = 0.03
    words  = []
    words_missing_in_tfidf = []
    for i in range(0, len(corpus)):
        bow = corpus[i]
        low_value_words = [] #reinitialize to be safe. You can skip this.
        tfidf_ids = [id for id, value in tfidf[bow]]
        bow_ids = [id for id, value in bow]
        low_value_words = [id for id, value in tfidf[bow] if value < low_value]
        drops = low_value_words+words_missing_in_tfidf
        for item in drops:
            words.append(id2word[item])
        words_missing_in_tfidf = [id for id in bow_ids if id not in tfidf_ids] # The words with tf-idf socre 0 will be missing

        new_bow = [b for b in bow if b[0] not in low_value_words and b[0] not in words_missing_in_tfidf]
        corpus[i] = new_bow
    return id2word, texts, corpus

In [101]:
data_words = list(sent_to_words(clean_sentence))
data_final = data_bigrams_trigrams(data_words)
id2word, texts, corpus = prep_for_lda_gensim(data_final, 0.03)

In [102]:
lda_model = gensim.models.ldamulticore.LdaMulticore(corpus=corpus[:-1],
                                           id2word=id2word,
                                           num_topics=50,
                                           random_state=100,
                                           #update_every=1,
                                           chunksize=100,
                                           passes=10, workers = os.cpu_count())
                                           #alpha="auto")

In [103]:
vis = pyLDAvis.gensim_models.prepare(lda_model,corpus, id2word, mds='mmds')
pyLDAvis.display(vis)

D:\Program Files (x86)\Python\lib\site-packages\pyLDAvis\_prepare.py:247: FutureWarning: In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only
  by='saliency', ascending=False).head(R).drop('saliency', 1)


In [242]:
lda = topic_visualization(data = df_sentence_final_2 , number_of_topics = 50)
#pyLDAvis.save_html(lda, 'lda.html')
pyLDAvis.display(lda)

In [7]:
df = pd.read_csv('trial_data/AAPL.csv')
data = pd.DataFrame({0:df['content']})

In [8]:
# Process by Sentence

pool = mp.Pool(processes=mp.cpu_count(), 
               initializer=clean_parallel_init.work, 
               initargs=(data[0],))
values = pool.imap(cpt.clean_mlm_init, range(0,len(data[0])))
result = []
for i in values:
    result.append(i)

pool.close()

In [9]:
result_df_g = pd.DataFrame({'text':result})
result_df_g = result_df_g['text'].explode()
#result_df_g_words = [[text for text in doc.split(" ")] for doc in result_df_g]
result_df_bt = data_bigrams_trigrams(result_df_g)

In [30]:
corpus_2 = corpora.Dictionary(result_df_bt)

In [31]:
corpus_bow = [corpus_2.doc2bow(doc, allow_update=True) for doc in result_df_bt]

In [32]:
word_counts = [[(corpus_2[id], count) for id, count in line] for line in corpus_bow]

In [33]:
lda_self = gensim.models.ldamulticore.LdaMulticore(corpus = corpus_bow,
                                                   id2word = corpus_2,
                                                   num_topics = 50,
                                                   random_state=100,
                                                   chunksize=100,
                                                   passes=10)
vis_self = pyLDAvis.gensim_models.prepare(lda_self, corpus_bow,corpus_2, mds='mmds')
pyLDAvis.display(vis_self)

D:\Program Files (x86)\Python\lib\site-packages\pyLDAvis\_prepare.py:247: FutureWarning: In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only
  by='saliency', ascending=False).head(R).drop('saliency', 1)


In [ ]:
#######################################################################################

In [10]:
corpus_2_f = corpora.Dictionary(result_df_bt)

In [11]:
corpus_2_f.filter_extremes(no_below = 10, no_above=0.1)

In [12]:
corpus_bow_filter = [corpus_2_f.doc2bow(doc) for doc in result_df_bt]
word_counts_filter = [[(corpus_2_f[id], count) for id, count in line] for line in corpus_bow_filter]

In [13]:
lda_self_f = gensim.models.ldamulticore.LdaMulticore(corpus = corpus_bow_filter,
                                                   id2word = corpus_2_f,
                                                   num_topics = 50,
                                                   random_state=100,
                                                   chunksize=100,
                                                   passes=10)
vis_self_f = pyLDAvis.gensim_models.prepare(lda_self_f, 
                                            corpus_bow_filter,
                                            corpus_2_f, mds='mmds')
pyLDAvis.display(vis_self_f)

D:\Program Files (x86)\Python\lib\site-packages\pyLDAvis\_prepare.py:247: FutureWarning: In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only
  by='saliency', ascending=False).head(R).drop('saliency', 1)


In [14]:
df_mid = pd.DataFrame({"Original text":split_sentence_nltk(data[0])})
#df_end = df_end.reset_index(drop=True)
df_end = pd.DataFrame({'Original text':df_mid['Original text'].explode()})
#df_end = df_end.replace(r'^s*$', float('NaN'), regex = True).dropna()


In [15]:
df_end['cleaned'] = result_df_bt

In [16]:
df_end['topics'] = lda_self_f.get_document_topics(corpus_bow_filter)

In [17]:
df1 = pd.DataFrame(list(df_end['topics'].explode()),columns=['t','p'],index=df_end['topics'].explode().index)
df1['index'] = df1.index

In [18]:
df_w_topics = pd.pivot_table(df1,
              index = 'index',
              values = 'p',
              columns = 't',
              fill_value = 0)

In [19]:
df_w_topics = df_w_topics.join(df_end[['cleaned',"Original text"]])

In [20]:
df_w_topics

0         1         2         3         4         5         6  \
0     0.072485  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000   
1     0.115973  0.081440  0.074371  0.159827  0.043073  0.197302  0.076818   
1     0.115973  0.081440  0.074371  0.159827  0.043073  0.197302  0.076818   
1     0.115973  0.081440  0.074371  0.159827  0.043073  0.197302  0.076818   
1     0.115973  0.081440  0.074371  0.159827  0.043073  0.197302  0.076818   
...        ...       ...       ...       ...       ...       ...       ...   
2996  0.320936  0.104681  0.108630  0.095765  0.503687  0.106745  0.198627   
2996  0.320936  0.104681  0.108630  0.095765  0.503687  0.106745  0.198627   
2997  0.000000  0.000000  0.000000  0.000000  0.000000  0.065093  0.103260   
2998  0.000000  0.000000  0.000000  0.000000  0.000000  0.159693  0.000000   
2999  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000  0.106215   

             7         8         9  ...        42        43        44  \
0     0.000000  0.000000  0.000000  ...  0.000000  0.000000  0.000000   
1     0.055837  0.169488  0.148887  ...  0.108212  0.120563  0.202429   
1     0.055837  0.169488  0.148887  ...  0.108212  0.120563  0.202429   
1     0.055837  0.169488  0.148887  ...  0.108212  0.120563  0.202429   
1     0.055837  0.169488  0.148887  ...  0.108212  0.120563  0.202429   
...        ...       ...       ...  ...       ...       ...       ...   
2996  0.158226  0.063407  0.179570  ...  0.142912  0.278539  0.000000   
2996  0.158226  0.063407  0.179570  ...  0.142912  0.278539  0.000000   
2997  0.000000  0.069481  0.000000  ...  0.114194  0.083377  0.000000   
2998  0.000000  0.000000  0.000000  ...  0.000000  0.000000  0.000000   
2999  0.092973  0.000000  0.000000  ...  0.000000  0.000000  0.000000   

            45        46        47        48        49  \
0     0.000000  0.000000  0.458556  0.000000  0.169492   
1     0.206088  0.108120  0.203663  0.181747  0.185297   
1     0.206088  0.108120  0.203663  0.181747  0.185297   
1     0.206088  0.108120  0.203663  0.181747  0.185297   
1     0.206088  0.108120  0.203663  0.181747  0.185297   
...        ...       ...       ...       ...       ...   
2996  0.093613  0.271524  0.093621  0.196737  0.120461   
2996  0.093613  0.271524  0.093621  0.196737  0.120461   
2997  0.064730  0.000000  0.000000  0.000000  0.255444   
2998  0.000000  0.000000  0.000000  0.000000  0.000000   
2999  0.000000  0.000000  0.098606  0.000000  0.000000   

                                                cleaned  \
0     [dow_jones, future, signal, market, rally, rev...   
1                [article, first, appear_morning_brief]   
1     [get_morning_brief, send_directly_inbox, every...   
1                                                  [et]   
1     [subscribe_monday, february, corporate_america...   
...                                                 ...   
2996            [today_download_best, stock, next, day]   
2996  [click_get_free, report, apple, inc, aapl, fre...   
2997  [yahoo_finance, brian_sozzi, julie_hyman, spea...   
2998  [company, would, crush, revenue, profit, estim...   
2999  [investor, observe, soar, price, technology, s...   

                                          Original text  
0     Dow Jones futures signal a market rally revers...  
1     This article first appeared in the Morning Brief.  
1     Get the Morning Brief sent directly to your in...  
1                                                   ET.  
1     Subscribe\n\nMonday, February 28, 2022\n\nCorp...  
...                                                 ...  
2996  Today, you can download 7 Best Stocks for the ...  
2996  Click to get this free report\r\n\r\nApple Inc...  
2997  Yahoo Finance’s Brian Sozzi and Julie Hyman sp...  
2998  The company would have crushed revenue and pro...  
2999  Investors who have observed soaring prices in ...  

[71547 rows x 52 columns]

In [24]:
import yfinance as yf
from yahoofinancials import YahooFinancials

In [26]:
def a():
    aapl_df = yf.download('AAPL', 
                      start='2019-01-01', 
                      end='2021-06-12', 
                      progress=True,)
    return aapl_df

In [39]:
%timeit a()

[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
268 ms ± 93.8 ms per loop (mean ± std. dev. of 7 runs, 1 loop each)


In [40]:
def b():
    yahoo_financials = YahooFinancials('AAPL')
    data = yahoo_financials.get_historical_price_data(start_date='2019-01-01', 
                                                  end_date='2019-12-31', 
                                                  time_interval='weekly')
    aapl_df = pd.DataFrame(data['AAPL']['prices'])
    aapl_df = aapl_df.drop('date', axis=1).set_index('formatted_date')
    return aapl_df

In [41]:
%timeit b()

D:\Program Files (x86)\Python\lib\site-packages\yahoofinancials\__init__.py:325: DeprecationWarning: UrlOpener style of invoking requests is deprecated. Use newer urlopen functions/methods
  urlopener = UrlOpener()
D:\Program Files (x86)\Python\lib\site-packages\yahoofinancials\__init__.py:325: DeprecationWarning: UrlOpener style of invoking requests is deprecated. Use newer urlopen functions/methods
  urlopener = UrlOpener()
D:\Program Files (x86)\Python\lib\site-packages\yahoofinancials\__init__.py:325: DeprecationWarning: UrlOpener style of invoking requests is deprecated. Use newer urlopen functions/methods
  urlopener = UrlOpener()
D:\Program Files (x86)\Python\lib\site-packages\yahoofinancials\__init__.py:325: DeprecationWarning: UrlOpener style of invoking requests is deprecated. Use newer urlopen functions/methods
  urlopener = UrlOpener()
D:\Program Files (x86)\Python\lib\site-packages\yahoofinancials\__init__.py:325: DeprecationWarning: UrlOpener style of invoking requests is

D:\Program Files (x86)\Python\lib\site-packages\yahoofinancials\__init__.py:325: DeprecationWarning: UrlOpener style of invoking requests is deprecated. Use newer urlopen functions/methods
  urlopener = UrlOpener()
D:\Program Files (x86)\Python\lib\site-packages\yahoofinancials\__init__.py:325: DeprecationWarning: UrlOpener style of invoking requests is deprecated. Use newer urlopen functions/methods
  urlopener = UrlOpener()
D:\Program Files (x86)\Python\lib\site-packages\yahoofinancials\__init__.py:325: DeprecationWarning: UrlOpener style of invoking requests is deprecated. Use newer urlopen functions/methods
  urlopener = UrlOpener()
D:\Program Files (x86)\Python\lib\site-packages\yahoofinancials\__init__.py:325: DeprecationWarning: UrlOpener style of invoking requests is deprecated. Use newer urlopen functions/methods
  urlopener = UrlOpener()
D:\Program Files (x86)\Python\lib\site-packages\yahoofinancials\__init__.py:325: DeprecationWarning: UrlOpener style of invoking requests is

D:\Program Files (x86)\Python\lib\site-packages\yahoofinancials\__init__.py:325: DeprecationWarning: UrlOpener style of invoking requests is deprecated. Use newer urlopen functions/methods
  urlopener = UrlOpener()
D:\Program Files (x86)\Python\lib\site-packages\yahoofinancials\__init__.py:325: DeprecationWarning: UrlOpener style of invoking requests is deprecated. Use newer urlopen functions/methods
  urlopener = UrlOpener()
D:\Program Files (x86)\Python\lib\site-packages\yahoofinancials\__init__.py:325: DeprecationWarning: UrlOpener style of invoking requests is deprecated. Use newer urlopen functions/methods
  urlopener = UrlOpener()


The slowest run took 5.29 times longer than the fastest. This could mean that an intermediate result is being cached.
245 ms ± 180 ms per loop (mean ± std. dev. of 7 runs, 10 loops each)


In [42]:
apl_df = b()
apl_df.head()

D:\Program Files (x86)\Python\lib\site-packages\yahoofinancials\__init__.py:325: DeprecationWarning: UrlOpener style of invoking requests is deprecated. Use newer urlopen functions/methods
  urlopener = UrlOpener()


high        low       open      close     volume  \
formatted_date                                                          
2019-01-01      39.712502  35.500000  38.722500  36.982498  966947200   
2019-01-08      38.632500  37.130001  37.389999  37.500000  725470000   
2019-01-15      39.470001  37.512501  37.567501  39.205002  491411200   
2019-01-22      39.532501  37.924999  39.102501  39.075001  554774800   
2019-01-29      42.915001  38.527500  39.062500  42.812500  830400800   

                 adjclose  
formatted_date             
2019-01-01      35.856091  
2019-01-08      36.357830  
2019-01-15      38.010899  
2019-01-22      37.884865  
2019-01-29      41.508522

In [48]:
import requests

In [46]:
def save_news(ticker_list):
    for ticker in ticker_list:
        r = requests.get(
            f'https://eodhistoricaldata.com/api/news?api_token=621cdd2196c0b8.92217368&s={ticker}&to=2022-01-01&offset=0&limit=1000')
        x = r.json()
        df = pd.DataFrame(x)
        last_date = df['date'][len(df) - 1][:10]
        for _ in range(0, 2):  # while last_date[:4] != "2015"
            r = requests.get(
                f'https://eodhistoricaldata.com/api/news?api_token=621cdd2196c0b8.92217368&s={ticker}&offset=0&limit=1000&to={last_date}')
            x = r.json()
            df_temp = pd.DataFrame(x)
            df = pd.concat([df, df_temp], ignore_index=True)
            last_date = df['date'][len(df) - 1][:10]
        ticker_df = yf.download(ticker, 
                      start=last_date, 
                      end='2022-01-01', 
                      progress=True,)
        ticker_df.to_csv(f"trial_data/{ticker}_market.csv")
        df.to_csv(f"trial_data/{ticker}_news.csv")

In [97]:
r = requests.get(
            f'https://eodhistoricaldata.com/api/news?api_token=621cdd2196c0b8.92217368&s=GM&offset=0&limit=1000')
x = r.json()
df_gm = pd.DataFrame(x)

In [104]:
df_gm.head(15)

date  \
0   2022-03-21T15:00:00+00:00   
1   2022-03-21T15:00:00+00:00   
2   2022-03-21T14:17:40+00:00   
3   2022-03-21T13:50:03+00:00   
4   2022-03-21T11:00:00+00:00   
5   2022-03-21T11:00:00+00:00   
6   2022-03-20T14:19:46+00:00   
7   2022-03-18T22:03:30+00:00   
8   2022-03-18T20:56:41+00:00   
9   2022-03-18T20:37:52+00:00   
10  2022-03-18T20:33:25+00:00   
11  2022-03-18T20:33:21+00:00   
12  2022-03-18T10:51:40+00:00   
13  2022-03-18T10:30:00+00:00   
14  2022-03-17T21:45:09+00:00   

                                                title  \
0   Axalta Mobility named a 2021 General Motors Su...   
1   Axalta Mobility named a 2021 General Motors Su...   
2   Volkswagen exec on the electric VW bus: 'I’ve ...   
3   General Motors to buy SoftBank’s stake in Crui...   
4   Dana Named 'Overdrive' Award Winner by General...   
5   Tenneco Named a 2021 Supplier of the Year by G...   
6       10 Cheap Stocks Hedge Funds Are Talking About   
7   GM Buys SoftBank’s $2.1 Billion Stake in Cruis...   
8   Electric vehicles: ‘We’ve seen a fairly steep ...   
9   GM buys SoftBank Vision Fund's stake in Cruise...   
10  UPDATE 3-GM bets $3.5 bln more on self-driving...   
11  GM to buy Softbank's stake in Cruise for $2.1 ...   
12  Tesla could eventually make flying aircrafts: ...   
13  Aspen Aerogels Named Overdrive Award Winner by...   
14  General Motors Company (GM) Stock Sinks As Mar...   

                                              content  \
0   CLINTON TOWNSHIP, Mich., March  21, 2022  (GLO...   
1   Axalta Coating Systems LLC\n\nAxalta - 2021 GM...   
2   Volkswagen Group of America President and CEO ...   
3   Yahoo Finance Live's Julie Hyman and Brian Soz...   
4   MAUMEE, Ohio, March 21, 2022 /PRNewswire/ -- D...   
5   LAKE FOREST, Ill., March 21, 2022 /PRNewswire/...   
6   In this article, we discuss 10 cheap stocks he...   
7   (Bloomberg) -- General Motors Co. bought out t...   
8   Jessica Caldwell, executive director of insigh...   
9   By David Shepardson and Aishwarya Nair\n\nWASH...   
10  (Add SoftBank's previous investment in Cruise,...   
11  General Motors Co. is making a bigger bet on i...   
12  In its third act, Tesla (TSLA) could find itse...   
13  PyroThin® Aerogel Technology Incorporated into...   
14  General Motors Company (GM) closed the most re...   

                                                 link  \
0   https://www.globenewswire.com/news-release/202...   
1   https://finance.yahoo.com/news/axalta-mobility...   
2   https://finance.yahoo.com/video/volkswagen-exe...   
3   https://finance.yahoo.com/video/general-motors...   
4   https://finance.yahoo.com/news/dana-named-over...   
5   https://finance.yahoo.com/news/tenneco-named-2...   
6   https://finance.yahoo.com/news/10-cheap-stocks...   
7   https://finance.yahoo.com/news/gm-buys-softban...   
8   https://finance.yahoo.com/video/electric-vehic...   
9   https://ca.finance.yahoo.com/news/gm-buys-soft...   
10  https://finance.yahoo.com/news/3-gm-bets-3-5-2...   
11  https://finance.yahoo.com/m/74519783-963e-3438...   
12  https://finance.yahoo.com/news/tesla-could-eve...   
13  https://finance.yahoo.com/news/aspen-aerogels-...   
14  https://finance.yahoo.com/news/general-motors-...   

                                              symbols  \
0                                    [GM.US, AXTA.US]   
1                             [GM.US, AXTA.US, 9AX.F]   
2   [TSLA.US, RIDE.US, GM.US, TM.US, F.US, VWAGY.U...   
3          [GM.US, SFTBY.US, GM.MX, GMCO34.SA, 8GM.F]   
4     [GM.US, DAN.US, GM.MX, GMCO34.SA, 8GM.F, 4DH.F]   
5                              [TEN.US, TNN.F, GM.US]   
6   [PFE.US, GM.US, INTC.US, CMCSA.US, TPNTF.US, W...   
7                    [GM.US, GM.MX, GMCO34.SA, 8GM.F]   
8   [TSLA.US, GM.US, NKLA.US, F.US, VWAGY.US, FDMO...   
9   [GM.US, SFTBY.US, GM.MX, GMCO34.SA, SFTBF.US, ...   
10  [GM.US, WMT.US, SFTBY.US, WALM34.SA, GM.MX, GM...   
11  [GM.US, SFTBY.US, GM.MX, GMCO34.SA, SFTBF.US, ...   
12  [TSLA.US, NI

In [49]:
save_news(['AMZN'])

[*********************100%***********************]  1 of 1 completed


In [80]:
df_market = pd.read_csv('trial_data/AMZN_market.csv')
df_news = pd.read_csv('trial_data/AMZN_news.csv')
#df_news['date'] = pd.to_datetime(df_news['date'])
#df_news['date'] = df_news['date'].dt.strftime('%Y-%m-%d')

In [96]:
df_news.loc[0]

Unnamed: 0                                                    0
date                                  2022-01-01T13:15:00+00:00
title                      Is It Too Late to Buy Shopify Stock?
content       Shopify (NYSE: SHOP) has generated massive ret...
link          https://finance.yahoo.com/m/a516b4d1-2e7d-3180...
symbols       ['AMZN.US', 'SHOP.US', 'AMZO34.SA', 'AMZ.XETRA...
tags                                                ['SHOPIFY']
Name: 0, dtype: object

In [82]:
df_market

Date         Open         High          Low        Close  \
0   2021-09-20  3396.000000  3419.000000  3305.010010  3355.729980   
1   2021-09-21  3375.000000  3379.699951  3332.389893  3343.629883   
2   2021-09-22  3351.000000  3389.000000  3341.050049  3380.050049   
3   2021-09-23  3380.050049  3428.959961  3380.050049  3416.000000   
4   2021-09-24  3402.010010  3429.260010  3393.399902  3425.520020   
..         ...          ...          ...          ...          ...   
68  2021-12-27  3420.739990  3458.860107  3384.310059  3393.389893   
69  2021-12-28  3403.649902  3443.520020  3382.709961  3413.219971   
70  2021-12-29  3416.800049  3424.239990  3372.010010  3384.020020   
71  2021-12-30  3394.000000  3417.760010  3370.479980  3372.889893   
72  2021-12-31  3379.120117  3387.000000  3331.169922  3334.340088   

      Adj Close   Volume  
0   3355.729980  4669100  
1   3343.629883  2780900  
2   3380.050049  2411400  
3   3416.000000  2379400  
4   3425.520020  2116200  
..          ...      ...  
68  3393.389893  2934400  
69  3413.219971  2731900  
70  3384.020020  1787700  
71  3372.889893  1879200  
72  3334.340088  2391500  

[73 rows x 7 columns]

In [37]:
ticker.recommendations

Firm      To Grade From Grade Action
Date                                                                    
2012-02-09 08:17:00    Canaccord Genuity           Buy              main
2012-03-08 07:33:00       FBN Securities    Outperform              main
2012-03-13 06:08:00            Jefferies           Buy              main
2012-03-14 06:13:00       Morgan Stanley    Overweight              main
2012-03-14 08:21:00    Canaccord Genuity           Buy              main
...                                  ...           ...        ...    ...
2022-01-28 14:19:01  New Street Research       Neutral       Sell     up
2022-01-28 15:10:56          Oppenheimer    Outperform              main
2022-01-31 15:44:19        Credit Suisse       Neutral              main
2022-02-15 15:31:58    Tigress Financial    Strong Buy              main
2022-03-11 11:57:08             Barclays  Equal-Weight              main

[831 rows x 4 columns]

In [36]:
aapl_df.columns

Index(['Open', 'High', 'Low', 'Close', 'Volume', 'Dividends', 'Stock Splits'], dtype='object')

In [20]:
lda_model = gensim.models.ldamulticore.LdaMulticore(corpus=corpus[:-1],
                                           id2word=id2word,
                                           num_topics=50,
                                           random_state=100,
                                           #update_every=1,
                                           chunksize=100,
                                           passes=10, workers = os.cpu_count())
                                           #alpha="auto")

In [21]:
vis = pyLDAvis.gensim_models.prepare(lda_model,corpus, id2word, mds='mmds')
pyLDAvis.display(vis)

D:\Program Files (x86)\Python\lib\site-packages\pyLDAvis\_prepare.py:247: FutureWarning: In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only
  by='saliency', ascending=False).head(R).drop('saliency', 1)


In [68]:
def topic_analysis (data, number_of_topics = 10):
        
        vectorizer = CountVectorizer(max_df=0.60, min_df=5)
        
        clean = vectorizer.fit_transform(data)
        
        feature_names = vectorizer.get_feature_names_out()
        
        lda = LatentDirichletAllocation(n_components=number_of_topics,
                                        #learning_method = 'online',
                                        #learning_decay=0.7,
                                        #learning_offset = 10,
                                        #batch_size = 256,
                                        #max_iter = 30,
                                        #evaluate_every = 10,
                                        #verbose=1,
                                        random_state=27, 
                                        n_jobs=-1)
        lda.fit(clean)
        
        topic_df = display_topics (lda, feature_names, 30)
        return (topic_df, lda, clean, feature_names)
    
def topic_visualization (data, number_of_topics=10):
        
        topic_df, lda, clean, feature_names = topic_analysis(data = data, number_of_topics = number_of_topics)
        
        topic_term_dists = lda.components_ / lda.components_.sum(axis=1)[:, None]
        doc_lengths = clean.sum(axis=1).getA1()
        term_frequency = clean.sum(axis=0).getA1()
        lda_doc_topic_dists = lda.transform(clean)
        doc_topic_dists = lda_doc_topic_dists / lda_doc_topic_dists.sum(axis=1)[:, None]
        vocab = feature_names
        
        lda_pyldavis = pyLDAvis.prepare(topic_term_dists, doc_topic_dists, doc_lengths, vocab, term_frequency)
        return(lda_pyldavis)

In [43]:
for i in range(0,len(data)):
    for j in range(0,len(result[i])):
        result[i][j] = " ".join(result[i][j])

In [50]:
result_df = pd.DataFrame({'text':result})
result_df = result_df['text'].explode()

In [122]:
vectorizer = CountVectorizer(max_df=0.4, min_df=5)
        
clean = vectorizer.fit_transform(result_df)
        
feature_names = vectorizer.get_feature_names_out()
        
lda = LatentDirichletAllocation(n_components=50,
                                        #learning_method = 'online',
                                        #learning_decay=0.7,
                                        #learning_offset = 10,
                                        #batch_size = 256,
                                        #max_iter = 10,
                                        #evaluate_every = 10,
                                        verbose=1,
                                        random_state=27, 
                                        n_jobs=-1)
lda.fit(clean)

iteration: 1 of max_iter: 10
iteration: 2 of max_iter: 10
iteration: 3 of max_iter: 10
iteration: 4 of max_iter: 10
iteration: 5 of max_iter: 10
iteration: 6 of max_iter: 10
iteration: 7 of max_iter: 10
iteration: 8 of max_iter: 10
iteration: 9 of max_iter: 10
iteration: 10 of max_iter: 10


LatentDirichletAllocation(n_components=50, n_jobs=-1, random_state=27,
                          verbose=1)

In [123]:
values = lda.transform(clean)

In [105]:
result_df[2]

'dow jones future signal market rally reversal west ramps sanction vs russia bank amid ongoing ukraine invasion'

In [275]:
list(chain.from_iterable(df_end.topics))

[(1, 0.25405544),
 (12, 0.07134707),
 (16, 0.0759246),
 (23, 0.06837732),
 (41, 0.06405532),
 (47, 0.26042405),
 (49, 0.1484695),
 (11, 0.34000164),
 (36, 0.33999568),
 (13, 0.17000371),
 (14, 0.6699865),
 (0, 0.01000016),
 (1, 0.01000016),
 (2, 0.01000016),
 (3, 0.01000016),
 (4, 0.01000016),
 (5, 0.01000016),
 (6, 0.01000016),
 (7, 0.01000016),
 (8, 0.01000016),
 (9, 0.01000016),
 (10, 0.01000016),
 (11, 0.01000016),
 (12, 0.01000016),
 (13, 0.01000016),
 (14, 0.01000016),
 (15, 0.01000016),
 (16, 0.01000016),
 (17, 0.01000016),
 (18, 0.01000016),
 (19, 0.01000016),
 (20, 0.01000016),
 (21, 0.01000016),
 (22, 0.01000016),
 (23, 0.01000016),
 (24, 0.01000016),
 (25, 0.01000016),
 (26, 0.01000016),
 (27, 0.01000016),
 (28, 0.01000016),
 (29, 0.01000016),
 (30, 0.01000016),
 (31, 0.01000016),
 (32, 0.01000016),
 (33, 0.01000016),
 (34, 0.01000016),
 (35, 0.01000016),
 (36, 0.01000016),
 (37, 0.01000016),
 (38, 0.5099921),
 (39, 0.01000016),
 (40, 0.01000016),
 (41, 0.01000016),
 (42, 0.

In [124]:
np.argmax(values[2])

32

In [126]:
topic_df = display_topics (lda, feature_names, 30)
    
topic_term_dists = lda.components_ / lda.components_.sum(axis=1)[:, None]
doc_lengths = clean.sum(axis=1).getA1()
term_frequency = clean.sum(axis=0).getA1()
lda_doc_topic_dists = lda.transform(clean)
doc_topic_dists = lda_doc_topic_dists / lda_doc_topic_dists.sum(axis=1)[:, None]
vocab = feature_names
        
lda_pyldavis = pyLDAvis.prepare(topic_term_dists, doc_topic_dists, doc_lengths, vocab, term_frequency)
pyLDAvis.display(lda_pyldavis)

In [95]:
vis2 = topic_visualization (result_df, number_of_topics=50)
pyLDAvis.display(vis2)

KeyboardInterrupt: 